# Message simulation for I2V Connectivity

The following corresponds to a test for simulating impact of vehicle-to-infrastructure (V2I) communication in traffic systems. 

## General description

For this application it is considered the simulation of microscopic traffic models where longitudinal position follow a specified behivior defined by two main components. The *car following* behavior describes the behavior of the vehicle in its longitudinal dynamics while the *lane change* behavior describes the behavior in the lateral position. 

In order to modify traffic behavior for a condition, the system is modeled via traffic model where V2I messages modify vehicle speed or lateral position   

### Car following behavior

For the sake of clarity, the following corresponds to the notations for variable description in the model. It is considered the vehicle position of a vehicle as $x_n$ and the headway space between a vehicle and its leader as $s_n = x_{n-1}-x_{n}$. The vehicle's speed and acceleration are defined as $v_n$,$a_n$ respectively.

For a determined vehicle in the network the longitudinal dynamics are determined by the acceleration behavior. In this case it is considred Tampere's Law. 

$$ 
a_n(t+T_n) = \min \left(c_{1,n-1}\Delta v_{n-1,n} + 
c_{2}\left(\Delta x_{n,n-1} - \left(s_0+\tau v_n(t)\right)\right),
c_{3}\left(v^\star(t) - v_n(t)\right)\right)
$$

One of the main features of this model is the adaptability to a specific speed condition, while preserving properties of the traffic such as the car following behavior in congestion situation. This feature makes it possible to trace features in the fundamental diagram. 

*To implement the model a `class` object called `Tampere` has been implemented. The class intends to describe the full behavior of the vehicle.* 

#### Parameters 

So far parameters in the model have been fixed although random scenarios can be also considered.

| Parameter     | Value     | Units |
:--------------:|:---------:|:------:
$$c_1,c_2,c_3$$ | 0.5       |
$$\tau$$        | $$\frac{1}{wk_x}$$ | [s]
$$w$$           | $$6.25$$  | [m/s]
$$k_x$$         | $$0.16$$  | [veh/km]
$$u_i$$         | $$25$$    | [m/s]

## Simulation Usage 

Inputs for simulation: 

The inputs for simulation are: 

* **Flow**: Vehicles are tested up to maximum capacity in free flow condition 
* **Market Penetration Rate (MPR)**: Penetration rate for connected vehicles 
* **Speed Drop**: Final speed limit for connected vehicles 


Some imports to be considered

In [1]:
from carfollow import Tampere, W_I, U_I, K_X
from support import leader_congestion_pattern, speed_change
import numpy as np

from plottools import plot_single_trace, plot_xva
from bokeh.plotting import figure, show, output_file
from bokeh.io import output_notebook
from bokeh.layouts import row, column

output_notebook()

Loading BokehJS ...

Main input definitions

In [12]:
Q_PERC = 2  # [0,1] Reduces flow, at 1 there's capacity.
N = 50  # 50 
SPEED_REDUCTION = 7  # Amount of speed reduction
MPR = 0.5  # Market penetration rate

Computing other constant values

In [13]:
# Constants

T_TOTAL = 720  # Simulation time
time = np.arange(T_TOTAL)  # Time vector

SHIFT_CONG = 450  # Congestion shift time appearing
PERCEP_RADIOUS = 100

# Scenario conditions
np.random.seed(42)  # Reproducibility
ID_CAV = np.random.randint(1, N - 1, int(N * MPR))  # Id Connected Vehicles
# ID_CAV = (2,)
D_CLASS = {k: "CAV" for k in ID_CAV}
V_CLASS = [D_CLASS.get(i, "HDV") for i in range(N)]  # All vehicle types
T_ACCEPT = SHIFT_CONG - np.random.exponential(PERCEP_RADIOUS, N * 1000)
T_ACCEPT = T_ACCEPT[(T_ACCEPT > 0) & (T_ACCEPT < SHIFT_CONG)]
T_ACCEPT = np.random.choice(T_ACCEPT, N)

# Vehicle Initial position / speed

X0 = np.flip(np.arange(0, N) * (W_I + U_I) / (W_I * K_X) * 1/Q_PERC)
V0 = np.ones(N) * U_I
A0 = np.zeros(N)

veh_list = []

# Initializing vehicles
Tampere.reset()
for x0, v0, vtype in zip(X0, V0, V_CLASS):
    veh_list.append(Tampere(x0, v0, 0 , vtype))

# Setting leader for vehicle i
for i in range(1, N):
    veh_list[i].set_leader(veh_list[i - 1])

Determining leader's acceleration

In [14]:
lead_acc = leader_congestion_pattern(time, shift=SHIFT_CONG)
acc = U_I + speed_change(time, SPEED_REDUCTION, 100)

In [15]:
# Matrix info storage
X = X0
V = V0
A = A0


for t, u in zip(time, lead_acc):
    for veh in veh_list:
        if veh.type == "CAV" and not veh.acc:
            t_accept = T_ACCEPT[veh.idx]
            # t_accept = 100
            if t >= t_accept:
                acc = U_I + speed_change(time, SPEED_REDUCTION, SHIFT_CONG - t)
                veh.register_control_speed(acc)
        veh.step_evolution(control=u)

    V = np.vstack((V, np.array([veh.v for veh in veh_list])))
    X = np.vstack((X, np.array([veh.x for veh in veh_list])))
    A = np.vstack((A, np.array([veh.a for veh in veh_list])))


In [16]:
leader = plot_single_trace(
    time, lead_acc, "Leaders' acceleration", "Time [secs]", "Acceleration [m/s²]"
)
spd_chg = plot_single_trace(time, acc, "Speed reduction", "Time [secs]", "Speed [m/s]")

pos, spd, acc = plot_xva(time, X, V, A)
show(column(row(leader, pos), row(spd, acc)))

A. Ladino